<a href="https://colab.research.google.com/github/syahrulg-lab/klasifikasi_hama/blob/main/01_klasifikasi_hama_sawit.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **LIBRARY**

In [1]:
# --- Google Colab: Mount Google Drive ---
from google.colab import drive
drive.mount('/content/drive')

# --- Install Library Tambahan ---
!pip install pyheif pillow pandas numpy openpyxl scikit-image onnxruntime

# --- Import Library ---
import os
import shutil
import cv2
import numpy as np
import pandas as pd
import pyheif
from PIL import Image
from skimage.feature import graycomatrix, graycoprops
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import (
    accuracy_score,
    precision_score,
    recall_score,
    f1_score,
    classification_report,
    confusion_matrix
)


Mounted at /content/drive
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.3/5.3 MB 48.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.5/16.5 MB 93.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 5.5 MB/s eta 0:00:00


# KONVERSI FILE HEIC JADI **JPG**

In [ ]:
# Ubah path ini ke lokasi folder utama di Google Drive Anda
base_folder = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original'

# Fungsi untuk konversi HEIC ke JPG
def convert_heic_to_jpg(heic_path, jpg_path):
    try:
        heif_file = pyheif.read(heic_path)
        image = Image.frombytes(
            heif_file.mode,
            heif_file.size,
            heif_file.data,
            "raw",
            heif_file.mode,
            heif_file.stride,
        )
        image.save(jpg_path, "JPEG")
        print(f"Converted: {heic_path} -> {jpg_path}")
    except ValueError:
        print(f"Skipping file {heic_path}: Not a valid HEIC/AVIF file")

# Loop semua sub-folder dan file
for root, dirs, files in os.walk(base_folder):
    for file in files:
        if file.lower().endswith('.heic'):
            heic_file_path = os.path.join(root, file)
            jpg_file_path = os.path.splitext(heic_file_path)[0] + '.jpg'

            # Konversi file
            convert_heic_to_jpg(heic_file_path, jpg_file_path)

Converted: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8185.HEIC -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8185.jpg
Converted: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8183.HEIC -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8183.jpg
Converted: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8184.HEIC -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8184.jpg
Converted: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8181.HEIC -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8181.jpg
Converted: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8180.HEIC -> /content/drive/My Drive/Data Penelitian/Kla

In [ ]:
# Mount Google Drive
drive.mount('/content/drive')

# Fungsi untuk memindahkan file JPG ke folder baru dengan struktur subfolder yang sama
def move_jpg_files(input_folder_path, output_folder_path):
    # List semua file dan subfolder
    for subdir, _, files in os.walk(input_folder_path):
        print(f"Checking subfolder: {subdir}")  # Debugging: Cek subfolder yang sedang diproses

        # Tentukan subfolder baru berdasarkan nama subfolder asal
        relative_subdir = os.path.relpath(subdir, input_folder_path)  # Relative path subfolder
        output_subdir = os.path.join(output_folder_path, relative_subdir)  # Membuat subfolder di folder output

        # Pastikan subfolder output ada untuk file JPG
        if not os.path.exists(output_subdir):
            os.makedirs(output_subdir)

        # Menampilkan file yang ada dalam subfolder untuk debugging
        print(f"Found {len(files)} files in {subdir}")

        for file in files:
            # Cek apakah file adalah JPG (misalnya .jpg atau .jpeg)
            if file.lower().endswith(('jpg', 'jpeg')):
                input_jpg_path = os.path.join(subdir, file)
                output_jpg_path = os.path.join(output_subdir, file)  # Menentukan path file JPG di folder baru

                # Pindahkan file JPG ke folder output (subfolder yang sama)
                if not os.path.exists(output_jpg_path):
                    shutil.move(input_jpg_path, output_jpg_path)  # Memindahkan file JPG ke folder output
                    print(f"Moved {input_jpg_path} -> {output_jpg_path}")

# Tentukan path folder yang berisi gambar JPG dan folder tujuan
input_folder_path = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original'  # Ganti dengan folder yang berisi file JPG
output_folder_path = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Original.jpg'  # Ganti dengan folder tujuan untuk file JPG

# Verifikasi folder input ada
if not os.path.exists(input_folder_path):
    print(f"Input folder path does not exist: {input_folder_path}")
else:
    print(f"Input folder exists: {input_folder_path}")

# Pindahkan file JPG ke folder baru dengan struktur subfolder yang sama
move_jpg_files(input_folder_path, output_folder_path)


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Input folder exists: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original
Checking subfolder: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original
Found 0 files in /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original
Checking subfolder: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight
Found 820 files in /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight
Moved /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8185.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Original.jpg/Blight/IMG_8185.jpg
Moved /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Dataset_Original/Blight/IMG_8183.jpg -> /content/drive/My Drive/Data Penelitian/Kla

# **RESIZE**

In [ ]:
# Fungsi untuk resize semua file JPG di subfolder
def resize_images_in_subfolders(source_folder, target_folder, resize_target=(800, 800)):
    for root, _, files in os.walk(source_folder):
        for file in files:
            if file.lower().endswith('.jpg'):  # Filter file JPG
                source_file = os.path.join(root, file)

                # Buat path target dengan struktur yang sama
                relative_path = os.path.relpath(root, source_folder)
                target_dir = os.path.join(target_folder, relative_path)
                os.makedirs(target_dir, exist_ok=True)  # Buat folder jika belum ada

                target_file = os.path.join(target_dir, file)

                try:
                    # Load dan resize gambar
                    with Image.open(source_file) as img:
                        resized_img = img.resize(resize_target, Image.Resampling.LANCZOS)

                        # Simpan hasil resize ke folder target
                        resized_img.save(target_file, format='JPEG', quality=90)
                        print(f"Berhasil resize: {source_file} -> {target_file}")
                except Exception as e:
                    print(f"Error saat memproses {source_file}: {e}")

# Path folder sumber dan folder tujuan
source_dir = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Original.jpg'  # Folder sumber
target_dir = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Resized'  # Folder tujuan

# Ukuran target untuk resize
resize_target = (800, 800)  # Ganti ukuran sesuai kebutuhan

# Jalankan fungsi
resize_images_in_subfolders(source_dir, target_dir, resize_target)
print("Proses resize selesai.")


Berhasil resize: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Original.jpg/Blight/IMG_8185.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Resized/Blight/IMG_8185.jpg
Berhasil resize: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Original.jpg/Blight/IMG_8183.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Resized/Blight/IMG_8183.jpg
Berhasil resize: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Original.jpg/Blight/IMG_8184.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Resized/Blight/IMG_8184.jpg
Berhasil resize: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Original.jpg/Blight/IMG_8181.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Resized/Blight/IMG_8181.jpg
Berhasil resize: /content/drive/My D

# **CROP**

In [ ]:
# Fungsi untuk crop semua file JPG di subfolder
def crop_images_in_subfolders(source_folder, target_folder, crop_box):
    """
    Crop semua file JPG dalam subfolder dan menyimpan hasilnya di folder target.

    Args:
        source_folder (str): Path ke folder sumber.
        target_folder (str): Path ke folder tujuan.
        crop_box (tuple): Koordinat (left, upper, right, lower) untuk crop.
    """
    for root, _, files in os.walk(source_folder):
        for file in files:
            if file.lower().endswith('.jpg'):  # Filter file JPG
                source_file = os.path.join(root, file)

                # Buat path target dengan struktur yang sama
                relative_path = os.path.relpath(root, source_folder)
                target_dir = os.path.join(target_folder, relative_path)
                os.makedirs(target_dir, exist_ok=True)  # Buat folder jika belum ada

                target_file = os.path.join(target_dir, file)

                try:
                    # Load dan crop gambar
                    with Image.open(source_file) as img:
                        cropped_img = img.crop(crop_box)  # Crop gambar

                        # Simpan hasil crop ke folder target
                        cropped_img.save(target_file, format='JPEG', quality=90)
                        print(f"Berhasil crop: {source_file} -> {target_file}")
                except Exception as e:
                    print(f"Error saat memproses {source_file}: {e}")

# Path folder sumber dan folder tujuan
source_dir = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Resized'  # Folder sumber
target_dir = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Crop'  # Folder tujuan

# Box untuk crop (left, upper, right, lower)
crop_box = (200, 10, 600, 800)  # Ganti koordinat sesuai kebutuhan

# Jalankan fungsi
crop_images_in_subfolders(source_dir, target_dir, crop_box)
print("Proses crop selesai.")


Berhasil crop: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Resized/Blight/IMG_8185.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Crop/Blight/IMG_8185.jpg
Berhasil crop: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Resized/Blight/IMG_8183.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Crop/Blight/IMG_8183.jpg
Berhasil crop: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Resized/Blight/IMG_8184.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Crop/Blight/IMG_8184.jpg
Berhasil crop: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Resized/Blight/IMG_8181.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Crop/Blight/IMG_8181.jpg
Berhasil crop: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/

# **RENAME**

In [ ]:
# Fungsi untuk menyalin file JPG dan mengganti namanya sambil mempertahankan struktur folder
def copy_and_rename_images_maintain_structure(source_folder, target_folder):
    """
    Salin file JPG ke folder baru, pertahankan struktur subfolder, dan beri nama file sesuai nama subfolder asal.

    Args:
        source_folder (str): Path ke folder sumber.
        target_folder (str): Path ke folder tujuan.
    """
    for root, dirs, files in os.walk(source_folder):
        for dir_name in dirs:
            # Path subfolder sumber
            subfolder_path = os.path.join(root, dir_name)

            # Buat subfolder yang sama di folder tujuan
            relative_path = os.path.relpath(subfolder_path, source_folder)
            target_subfolder = os.path.join(target_folder, relative_path)
            os.makedirs(target_subfolder, exist_ok=True)

            # Ambil semua file JPG di subfolder
            jpg_files = [f for f in os.listdir(subfolder_path) if f.lower().endswith('.jpg')]

            # Proses file JPG dan salin ke subfolder tujuan
            for i, file in enumerate(jpg_files, start=1):  # Nomor urut dimulai dari 1
                source_file = os.path.join(subfolder_path, file)

                # Ganti nama file sesuai nama subfolder dan nomor urut
                new_file_name = f"{dir_name}_{i}.jpg"
                target_file = os.path.join(target_subfolder, new_file_name)

                # Salin file
                try:
                    shutil.copy(source_file, target_file)
                    print(f"Berhasil menyalin: {source_file} -> {target_file}")
                except Exception as e:
                    print(f"Error saat menyalin {source_file}: {e}")

# Path folder sumber dan folder tujuan
source_dir = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Crop'  # Folder sumber
target_dir = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename'  # Folder tujuan

# Jalankan fungsi
copy_and_rename_images_maintain_structure(source_dir, target_dir)
print("Proses penyalinan dan penggantian nama selesai.")


Berhasil menyalin: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Crop/Blight/IMG_8185.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename/Blight/Blight_1.jpg
Berhasil menyalin: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Crop/Blight/IMG_8183.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename/Blight/Blight_2.jpg
Berhasil menyalin: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Crop/Blight/IMG_8184.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename/Blight/Blight_3.jpg
Berhasil menyalin: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Crop/Blight/IMG_8181.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename/Blight/Blight_4.jpg
Berhasil menyalin: /content/drive/My Drive/Data Penelitian/Klasi

In [ ]:
# Mount Google Drive
drive.mount('/content/drive')

# Fungsi untuk memindahkan file JPG lebih dari 400 ke folder baru
def move_excess_jpg_files(input_folder_path, output_folder_path, limit=400):
    # List semua file dan subfolder
    for subdir, _, files in os.walk(input_folder_path):
        print(f"Checking subfolder: {subdir}")  # Debugging: Cek subfolder yang sedang diproses

        # Tentukan subfolder baru berdasarkan nama subfolder asal
        relative_subdir = os.path.relpath(subdir, input_folder_path)  # Relative path subfolder
        output_subdir = os.path.join(output_folder_path, relative_subdir)  # Membuat subfolder di folder output

        # Pastikan subfolder output ada
        if not os.path.exists(output_subdir):
            os.makedirs(output_subdir)

        # Filter hanya file JPG atau JPEG
        jpg_files = [file for file in files if file.lower().endswith(('jpg', 'jpeg'))]
        print(f"Found {len(jpg_files)} JPG files in {subdir}")

        # Jika jumlah file JPG lebih dari limit (misalnya 400), pindahkan sisanya
        if len(jpg_files) > limit:
            excess_files = jpg_files[limit:]  # Ambil file lebih dari batas yang ditentukan
            for file in excess_files:
                input_jpg_path = os.path.join(subdir, file)
                output_jpg_path = os.path.join(output_subdir, file)  # Menentukan path file JPG di folder baru

                # Pindahkan file JPG ke folder output (subfolder yang sama)
                shutil.move(input_jpg_path, output_jpg_path)  # Memindahkan file JPG ke folder output
                print(f"Moved {input_jpg_path} -> {output_jpg_path}")

# Tentukan path folder yang berisi gambar JPG dan folder tujuan
input_folder_path = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename'  # Ganti dengan folder asal yang berisi file JPG
output_folder_path = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Lebihan'  # Ganti dengan folder tujuan untuk file JPG lebih dari 400

# Verifikasi folder input ada
if not os.path.exists(input_folder_path):
    print(f"Input folder path does not exist: {input_folder_path}")
else:
    print(f"Input folder exists: {input_folder_path}")

# Pindahkan file JPG lebih dari 400 ke folder baru
move_excess_jpg_files(input_folder_path, output_folder_path)


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Input folder exists: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename
Checking subfolder: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename
Found 0 JPG files in /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename
Checking subfolder: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename/Blight
Found 410 JPG files in /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename/Blight
Moved /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename/Blight/Blight_401.jpg -> /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Lebihan/Blight/Blight_401.jpg
Moved /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Ren

# **EKSTRAKSI FITUR RGB STD, RGB MEAN, GLCM**

In [ ]:
# Fungsi ekstraksi fitur dari satu gambar
def extract_features(image_path):
    image = cv2.imread(image_path)
    image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    image_gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)

    # Ekstrak RGB Mean dan STD
    r_mean, g_mean, b_mean = np.mean(image_rgb[:, :, 0]), np.mean(image_rgb[:, :, 1]), np.mean(image_rgb[:, :, 2])
    r_std, g_std, b_std = np.std(image_rgb[:, :, 0]), np.std(image_rgb[:, :, 1]), np.std(image_rgb[:, :, 2])

    # GLCM (Gray Level Co-Occurrence Matrix)
    glcm = graycomatrix(image_gray, distances=[1], angles=[0], levels=256, symmetric=True, normed=True)
    contrast = graycoprops(glcm, 'contrast')[0, 0]
    energy = graycoprops(glcm, 'energy')[0, 0]
    homogeneity = graycoprops(glcm, 'homogeneity')[0, 0]
    entropy = -np.sum(glcm * np.log2(glcm + (glcm == 0)))  # Hindari log(0)

    return [r_mean, g_mean, b_mean, r_std, g_std, b_std, contrast, energy, homogeneity, entropy]

# Fungsi untuk memuat gambar dari subfolder
def load_dataset(base_folder):
    data = []
    labels = []
    file_names = []
    for root, dirs, files in os.walk(base_folder):
        for file in files:
            if file.lower().endswith(('.jpg', '.jpeg', '.png')):
                path = os.path.join(root, file)
                label = os.path.basename(root)
                features = extract_features(path)
                data.append(features)
                labels.append(label)
                file_names.append(file)
    return data, labels, file_names

# Ganti dengan path folder gambar di Google Drive
base_folder = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Preprocessing/Data_Rename'  # <- ganti sesuai kebutuhanmu

print("Ekstraksi fitur dimulai...")
data, labels, file_names = load_dataset(base_folder)
print("Ekstraksi selesai.")

# Buat DataFrame dan tambahkan kolom penomoran
columns = ['R_mean', 'G_mean', 'B_mean', 'R_std', 'G_std', 'B_std',
           'GLCM_Contrast', 'GLCM_Energy', 'GLCM_Homogeneity', 'GLCM_Entropy']
df = pd.DataFrame(data, columns=columns)
df['File_Name'] = file_names
df['Label'] = labels

# Tambahkan kolom "No" dari 1 sampai jumlah data
df.insert(0, 'No', range(1, len(df) + 1))  # Insert kolom No di posisi pertama

# Simpan ke Excel
output_path = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Output/Ekstraksifitur_RGBnGLCM.xlsx'
df.to_excel(output_path, index=False)
print(f"Fitur berhasil disimpan di: {output_path}")

Ekstraksi fitur dimulai...
Ekstraksi selesai.
Fitur berhasil disimpan di: /content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Output/Ekstraksifitur_RGBnGLCM.xlsx


# **KNN**

In [ ]:
datasetdaunsawit = '/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Output/Ekstraksifitur_RGBnGLCM.xlsx'
dataset = pd.read_excel(datasetdaunsawit)

# 1. Pisahkan fitur (X) dan target (y)
X = dataset.drop(columns=['File_Name', 'No', 'Label'])  # Fitur
y = dataset['Label']  # Target
file_names = dataset['File_Name']  # Simpan nama file

# 2. Bagi data menjadi data latih dan uji (70:30)
X_train, X_test, y_train, y_test, file_train, file_test = train_test_split(
    X, y, file_names, test_size=0.3, random_state=42)

# 3. Normalisasi data
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# 4. Latih model KNN
knn = KNeighborsClassifier(n_neighbors=5)
knn.fit(X_train, y_train)

# 5. Prediksi data uji
y_pred = knn.predict(X_test)

# 6. Evaluasi metrik
akurasi = accuracy_score(y_test, y_pred)
presisi = precision_score(y_test, y_pred, average='macro')
recall = recall_score(y_test, y_pred, average='macro')
f1 = f1_score(y_test, y_pred, average='macro')
cm = confusion_matrix(y_test, y_pred)
cr = classification_report(y_test, y_pred, output_dict=True)

# 7. Simpan hasil prediksi per data
df_hasil = pd.DataFrame({
    'File_Name': file_test.values,
    'Label Asli': y_test.values,
    'Prediksi': y_pred,
})
df_hasil['Benar/Salah'] = df_hasil['Label Asli'] == df_hasil['Prediksi']

# 8. Simpan ke Excel
with pd.ExcelWriter('/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Output/Hasil_KNN.xlsx') as writer:
    # Simpan prediksi
    df_hasil.to_excel(writer, sheet_name='Hasil Prediksi', index=False)

    # Metrik utama
    df_metrics = pd.DataFrame({
        'Metrik': ['Akurasi', 'Presisi', 'Recall', 'F1 Score'],
        'Nilai': [akurasi, presisi, recall, f1]
    })
    df_metrics.to_excel(writer, sheet_name='Metrik Utama', index=False)

    # Classification report
    df_cr = pd.DataFrame(cr).transpose()
    df_cr.to_excel(writer, sheet_name='Classification Report')

    # Confusion matrix
    df_cm = pd.DataFrame(cm,
                         index=[f"Actual_{label}" for label in knn.classes_],
                         columns=[f"Predicted_{label}" for label in knn.classes_])
    df_cm.to_excel(writer, sheet_name='Confusion Matrix')

print("Hasil lengkap evaluasi dan prediksi berhasil disimpan ke Excel.")


Hasil lengkap evaluasi dan prediksi berhasil disimpan ke Excel.


In [ ]:
# 1. Pisahkan fitur (X) dan target (y)
X = dataset.drop(columns=['File_Name', 'No', 'Label'])  # Fitur
y = dataset['Label']  # Target
file_names = dataset['File_Name']  # Simpan nama file

# 2. Bagi data menjadi data latih dan uji (70:30)
X_train, X_test, y_train, y_test, file_train, file_test = train_test_split(
    X, y, file_names, test_size=0.3, random_state=42)

# 3. Normalisasi data (opsional untuk Naive Bayes, tapi bisa bantu performa)
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# 4. Latih model Naive Bayes
nb = GaussianNB()
nb.fit(X_train, y_train)

# 5. Prediksi data uji
y_pred = nb.predict(X_test)

# 6. Evaluasi metrik
akurasi = accuracy_score(y_test, y_pred)
presisi = precision_score(y_test, y_pred, average='macro')
recall = recall_score(y_test, y_pred, average='macro')
f1 = f1_score(y_test, y_pred, average='macro')
cm = confusion_matrix(y_test, y_pred)
cr = classification_report(y_test, y_pred, output_dict=True)

# 7. Simpan hasil prediksi per data
df_hasil = pd.DataFrame({
    'File_Name': file_test.values,
    'Label Asli': y_test.values,
    'Prediksi': y_pred,
})
df_hasil['Benar/Salah'] = df_hasil['Label Asli'] == df_hasil['Prediksi']

# 8. Simpan semua hasil ke Excel
with pd.ExcelWriter('/content/drive/My Drive/Data Penelitian/KlasifikasiHamaSawit/Output/Hasil_NaiveBayes.xlsx') as writer:
    df_hasil.to_excel(writer, sheet_name='Hasil Prediksi', index=False)

    df_metrics = pd.DataFrame({
        'Metrik': ['Akurasi', 'Presisi', 'Recall', 'F1 Score'],
        'Nilai': [akurasi, presisi, recall, f1]
    })
    df_metrics.to_excel(writer, sheet_name='Metrik Utama', index=False)

    df_cr = pd.DataFrame(cr).transpose()
    df_cr.to_excel(writer, sheet_name='Classification Report')

    df_cm = pd.DataFrame(cm,
                         index=[f"Actual_{label}" for label in nb.classes_],
                         columns=[f"Predicted_{label}" for label in nb.classes_])
    df_cm.to_excel(writer, sheet_name='Confusion Matrix')

print("Hasil evaluasi Naive Bayes berhasil disimpan ke Excel.")


Hasil evaluasi Naive Bayes berhasil disimpan ke Excel.
